In [1]:
import requests
from pprint import pprint
import time
import pandas as pd

In [2]:
user = "Gotwiller"

In [3]:
df = pd.read_csv(f"../Data/{user}.csv")
max_timestamp = df['uts'].max()
max_timestamp

1764571939

## Liste des amis suivis

In [4]:
from pprint import pprint

api_key = "ea311d73665c24b237160f90bcb986ff"
artist = "Daft Punk"
method = "artist.getInfo"

url = f"http://ws.audioscrobbler.com/2.0/?method=user.getfriends&user={user}&api_key={api_key}&format=json"
# Envoi d'une requête GET
response = requests.get(url)

# Vérification du statut de la réponse
if response.status_code == 200:
    # Affichage des données JSON
    data = response.json()
    for user in data["friends"]["user"]:
        print(user["name"])
else:
    print(f"Erreur : {response.status_code}")

Mehdinho16
anessrb
LightAkabane
Kallikall
Boborlegamorf
amoham16
Cassy1508
Ayamathers
drikoooooo
tzisteph
Kronyx67
jardinier38
clara_llz
Petah_Parkour
Grimkujow
redneck2_0
GunLock38
Alxstg
Charloops
Iandir
IcaRio_
Shironekii
Watch77


In [ ]:
api_key = "ea311d73665c24b237160f90bcb986ff"
method = "user.getInfo"

url = f"http://ws.audioscrobbler.com/2.0/?method={method}&user={user}&api_key={api_key}&format=json"
# Envoi d'une requête GET
response = requests.get(url)

# Vérification du statut de la réponse
if response.status_code == 200:
    # Affichage des données JSON
    data = response.json()
    playcount = int(data["user"]["playcount"])
    pprint(playcount)
else:
    print(f"Erreur : {response.status_code}")

Erreur : 400


In [ ]:
api_key = "ea311d73665c24b237160f90bcb986ff"
method = "user.getrecenttracks"
limit = 200 
timestamp_start = 1756731733

all_tracks = []
page = 1
total_pages = playcount / 200 + 1

while page <= total_pages:
    url = f"http://ws.audioscrobbler.com/2.0/?method={method}&limit={limit}&user={user}&page={page}&from={timestamp_start}&api_key={api_key}&format=json"
    response = requests.get(url)
    
    if response.status_code == 200:
        data = response.json()
        tracks = data['recenttracks']['track']
        all_tracks.extend(tracks)
        
        # mise à jour du nombre total de pages
        total_pages = int(data['recenttracks']['@attr']['totalPages'])
        print(f"Page {page}/{total_pages} récupérée, total tracks: {len(all_tracks)}")
        
        page += 1
        time.sleep(0.2)  # pour ne pas spammer l'API
    else:
        print(f"Erreur à la page {page} : {response.status_code}")
        break

# Affichage final de tous les tracks récupérés
pprint(all_tracks)


Page 1/24 récupérée, total tracks: 201
Page 2/24 récupérée, total tracks: 402
Page 3/24 récupérée, total tracks: 603
Page 4/24 récupérée, total tracks: 804
Page 5/24 récupérée, total tracks: 1005
Page 6/24 récupérée, total tracks: 1206
Page 7/24 récupérée, total tracks: 1407
Page 8/24 récupérée, total tracks: 1608
Page 9/24 récupérée, total tracks: 1809
Page 10/24 récupérée, total tracks: 2010
Page 11/24 récupérée, total tracks: 2211
Page 12/24 récupérée, total tracks: 2412
Page 13/24 récupérée, total tracks: 2613
Page 14/24 récupérée, total tracks: 2814
Page 15/24 récupérée, total tracks: 3015
Page 16/24 récupérée, total tracks: 3216
Page 17/24 récupérée, total tracks: 3417
Page 18/24 récupérée, total tracks: 3618
Page 19/24 récupérée, total tracks: 3819
Page 20/24 récupérée, total tracks: 4020
Page 21/24 récupérée, total tracks: 4221
Page 22/24 récupérée, total tracks: 4421
Page 23/24 récupérée, total tracks: 4621
Page 24/24 récupérée, total tracks: 4785
[{'@attr': {'nowplaying': 'tr

## Changement de format

In [15]:
import csv

# Supposons que tes données JSON soient dans une liste appelée all_tracks
# all_tracks = [...]  # tes données JSON récupérées

output_file = "lastfm_tracks_filtered.csv"

with open(output_file, mode='w', newline='', encoding='utf-8') as f:
    writer = csv.writer(f)
    
    # Écriture de l'en-tête
    writer.writerow(["uts", "utc_time", "artist", "artist_mbid", "album", "album_mbid", "track", "track_mbid"])
    
    for track in all_tracks:
        # Exclure les tracks en cours de lecture
        nowplaying = track.get('@attr', {}).get('nowplaying', 'false')
        if nowplaying.lower() == 'true':
            continue  # passer au track suivant
        
        # Certains tracks peuvent ne pas avoir de date
        date_info = track.get("date", {})
        uts = date_info.get("uts", "")
        utc_time = date_info.get("#text", "")
        
        artist_name = track["artist"].get("#text", "")
        artist_mbid = track["artist"].get("mbid", "")
        album_name = track["album"].get("#text", "")
        album_mbid = track["album"].get("mbid", "")
        track_name = track.get("name", "")
        track_mbid = track.get("mbid", "")
        
        writer.writerow([uts, utc_time, artist_name, artist_mbid, album_name, album_mbid, track_name, track_mbid])

print(f"CSV généré sans les morceaux en lecture : {output_file}")


CSV généré sans les morceaux en lecture : lastfm_tracks_filtered.csv


## Concatenation csv

In [19]:
new_df = pd.read_csv("lastfm_tracks_filtered.csv")
old_df = pd.read_csv(f"../Data/{user}.csv")
combined_df = pd.concat([old_df, new_df]).drop_duplicates().reset_index(drop=True)
combined_df.to_csv(f"../Data/{user}.csv", index=False)